## 第7章: データベース
[artist.json.gz](http://www.cl.ecei.tohoku.ac.jp/nlp100/data/artist.json.gz)は，オープンな音楽データベース[MusicBrainz](https://musicbrainz.org/)の中で，アーティストに関するものをJSON形式に変換し，gzip形式で圧縮したファイルである．このファイルには，1アーティストに関する情報が1行にJSON形式で格納されている．JSON形式の概要は以下の通りである．


|          フィールド       |     型	  | 内容 | 例 | 
|:------------------------:|:----------:|:-------:|:-----:|
|            id            | ユニーク識別子 | 整数 |20660
|           gid	           | グローバル識別子 | 文字列	|"ecf9f3a3-35e9-4c58-acaa-e707fba45060"
|          name	           | アーティスト名| 	文字列	|"Oasis"
|        sort_name	       | アーティスト名 |（辞書順整列用）|	文字列	"Oasis"
|          area            | 活動場所  | 文字列 | "United Kingdom"
|        aliases	       | 別名	  |  辞書オブジェクトのリスト	|  .
|     aliases[].name       | 別名	  |  文字列 | "オアシス"
|  aliases[].sort_name     | 別名（整列用） | 文字列	| "オアシス"
|          begin	       | 活動開始日	|辞書	| .
|       begin.year	       |     活動開始年	|整数 | 1991
|      begin.month	       |     活動開始月	|整数	| .
|      begin.date	       |    活動開始日	|整数	| .
|         end              |       	活動終了日	|辞書	 | .
|       end.year	       |        活動終了年	|整数	 |2009
|       end.month	       |          活動終了月	| 整数	|8
|       end.date           |       	活動終了日	| 整数	|28
|         tags	           |        タグ|	辞書オブジェクトのリスト | .	
|      tags[].count	       |       タグ付けされた回数	|整数|	1
|     tags[].value	       |      タグ内容|	文字列	|"rock"
|       rating             |     	レーティング	|辞書オブジェクト | .	
|    rating.count	       |      レーティングの投票数|	整数|	13
|    rating.value	       |     レーティングの値（平均値）	|整数	|86


artist.json.gzのデータをKey-Value-Store (KVS) およびドキュメント志向型データベースに格納・検索することを考える．KVSとしては，[LevelDB](http://leveldb.org/)，[Redis](http://redis.io/)，[KyotoCabinet](http://fallabs.com/kyotocabinet/)等を用いよ．ドキュメント志向型データベースとして，[MongoDB](http://www.mongodb.org/)を採用したが，[CouchDB](http://couchdb.apache.org/)や[RethinkDB](http://rethinkdb.com/)等を用いてもよい．



# 60. KVSの構築
Key-Value-Store (KVS) を用い，アーティスト名（name）から活動場所（area）を検索するためのデータベースを構築せよ

In [139]:
import redis
import json

json_file = 'artist.json'

conn = redis.StrictRedis(host='localhost', port=6379,db=0)

with open(json_file, 'r')as f:
    for line in f:
        json_data = json.loads(line)
       
        key = json_data['name'] + '\t' + str(json_data['id'])
        if json_data.get('area'):
            value = json_data.get('area')
        else:
            value = ''
    
        conn.set(key.encode(), value.encode())
        

KeyboardInterrupt: 

# 61. KVSの検索
60で構築したデータベースを用い，特定の（指定された）アーティストの活動場所を取得せよ．

In [131]:
name = "Liis Viira"
key = conn.keys(name + '\t' + '*')[0]
print('area:', conn.get(key).decode())

area: Estonia


# 62. KVS内の反復処理
60で構築したデータベースを用い，活動場所が「Japan」となっているアーティスト数を求めよ．

In [70]:
i = 0
sum = [ name for name in conn.keys() if conn.get(name).decode() == 'Japan']
print('sum:', len(sum))

sum: 21946


# 63. オブジェクトを値に格納したKVS
KVSを用い，アーティスト名（name）からタグと被タグ数（タグ付けされた回数）のリストを検索するためのデータベースを構築せよ．さらに，ここで構築したデータベースを用い，アーティスト名からタグと被タグ数を検索せよ．



In [147]:
import redis
import json

json_file = 'artist.json'

conn = redis.StrictRedis(host='localhost', port=6379, db=1)

with open(json_file, 'r') as f:
    for line in f:
        json_data = json.loads(line)
        
        key = json_data['name'] + '\t' + str(json_data['id'])
        
        if json_data.get('tags'):
            tags = json_data.get('tags')
        else:
            tags = ''
        
        conn.set(key.encode(), tags)

In [175]:
name = 'Oasis'
key = conn.keys(name + '\t' + '*')[0]
print('tags:', conn.get(key).decode())


tags: 


# 64. MongoDBの構築
アーティスト情報（artist.json.gz）をデータベースに登録せよ．さらに，次のフィールドでインデックスを作成せよ: name, aliases.name, tags.value, rating.value

In [191]:
import pymongo
import json

json_file = 'artist.json'

conn = pymongo.MongoClient(host='localhost', port=27017)
db = conn.artists
co = db.info


with open(json_file, 'r') as f:
    for line in f:
        json_data = json.loads(line)
        co.insert_one(json_data)
        
        
co.create_index([('name', pymongo.ASCENDING)])
co.create_index([('aliases.name', pymongo.ASCENDING)])
co.create_index([('tags.value', pymongo.ASCENDING)])
co.create_index([('rating.value', pymongo.ASCENDING)])

# 65. MongoDBの検索
MongoDBのインタラクティブシェルを用いて，"Queen"というアーティストに関する情報を取得せよ．さらに，これと同様の処理を行うプログラムを実装せよ．

In [242]:
import pymongo
import json
from bson.objectid import ObjectId

conn = pymongo.MongoClient(host='localhost', port=27017)
db = conn.artists
co = db.info

def Chekc_ObjectId(obj):
    if isinstance(obj, ObjectId):
        return str(obj)
    raise TypeError(repr(obj) + "is not JSON serializable")


Queen = co.find({'name': 'Queen'})
for i in Queen:
    print(json.dumps(i, indent='\t', sort_keys=True, default=Chekc_ObjectId))

{
	"_id": "59853f0194b4bd7702721f38",
	"aliases": [
		{
			"name": "Queen",
			"sort_name": "Queen"
		}
	],
	"area": "Japan",
	"ended": true,
	"gender": "Female",
	"gid": "420ca290-76c5-41af-999e-564d7c71f1a7",
	"id": 701492,
	"name": "Queen",
	"sort_name": "Queen",
	"tags": [
		{
			"count": 1,
			"value": "kamen rider w"
		},
		{
			"count": 1,
			"value": "related-akb48"
		}
	],
	"type": "Character"
}
{
	"_id": "59853f1d94b4bd770272e5e4",
	"aliases": [
		{
			"name": "\u5973\u738b",
			"sort_name": "\u5973\u738b"
		}
	],
	"area": "United Kingdom",
	"begin": {
		"date": 27,
		"month": 6,
		"year": 1970
	},
	"ended": true,
	"gid": "0383dadf-2a4e-4d10-a46a-e9e041da8eb3",
	"id": 192,
	"name": "Queen",
	"rating": {
		"count": 24,
		"value": 92
	},
	"sort_name": "Queen",
	"tags": [
		{
			"count": 2,
			"value": "hard rock"
		},
		{
			"count": 1,
			"value": "70s"
		},
		{
			"count": 1,
			"value": "queen family"
		},
		{
			"count": 1,
			"value": "90s"
		},
		{
			"count": 1,
			"valu

# 66. 検索件数の取得
MongoDBのインタラクティブシェルを用いて，活動場所が「Japan」となっているアーティスト数を求めよ．

In [244]:
!mongo
!use artists
!co = db.info
!co.find({'area': 'Japan'}).length()

MongoDB shell version v3.4.6
connecting to: mongodb://127.0.0.1:27017
MongoDB server version: 3.4.6
Server has startup warnings: 
2017-08-05T12:24:42.750+0900 I CONTROL  [initandlisten] 
2017-08-05T12:24:42.750+0900 I CONTROL  [initandlisten] ** WARNING: Access control is not enabled for the database.
2017-08-05T12:24:42.751+0900 I CONTROL  [initandlisten] **          Read and write access to data and configuration is unrestricted.
2017-08-05T12:24:42.751+0900 I CONTROL  [initandlisten] 
> ^C
bye
/bin/sh: use: command not found
/bin/sh: co: command not found
/bin/sh: -c: line 0: syntax error near unexpected token `{'area':'
/bin/sh: -c: line 0: `co.find({'area': 'Japan'}).length()'


In [ ]:
import pymongo

conn = pymongo.MongoClient(host='localhost', port=27017)
db = conn.artists
co = db.info

Japan = co.find({'area': 'Japan'})

for i in Japan:
    print(json.dumps(i, indent='\t', sort_keys=True, default=Chekc_ObjectId))

{
	"_id": "59853d6f94b4bd770268e9dd",
	"area": "Japan",
	"ended": true,
	"gid": "6b45a7c4-e2f8-49ff-af57-b5829b4ed8bb",
	"id": 723554,
	"name": "Priest",
	"sort_name": "Priest",
	"tags": [
		{
			"count": 1,
			"value": "hello project related"
		}
	],
	"type": "Group"
}
{
	"_id": "59853d6f94b4bd770268ec24",
	"area": "Japan",
	"begin": {
		"date": 12,
		"month": 3,
		"year": 1965
	},
	"ended": true,
	"gender": "Male",
	"gid": "b62558bc-3753-46ba-9c62-793bd3d76251",
	"id": 883036,
	"name": "\u5927\u8cab\u548c\u7d00",
	"sort_name": "\u014cnuki, Kazunori",
	"type": "Person"
}
{
	"_id": "59853d6f94b4bd770268ec7f",
	"area": "Japan",
	"begin": {
		"date": 13,
		"month": 12,
		"year": 1978
	},
	"ended": true,
	"gender": "Male",
	"gid": "9c6870f8-c226-4727-bada-50d6360424d5",
	"id": 883037,
	"name": "\u798f\u5bcc\u96c5\u4e4b",
	"sort_name": "Fukutomi, Masayuki",
	"type": "Person"
}
{
	"_id": "59853d6f94b4bd770268ed0e",
	"area": "Japan",
	"ended": true,
	"gender": "Female",
	"gid": "660ced8e-94a

# 67. 複数のドキュメントの取得
特定の（指定した）別名を持つアーティストを検索せよ．

In [274]:
import pymongo
import json

def sort_name(name):

    conn = pymongo.MongoClient(host='localhost', port=27017)
    db = conn.artists
    co = db.info

    aliases = co.find({'aliases.name': name})

    for i, alias in enumerate(aliases, start=1):
        print('No', i)
        print(json.dumps(alias, indent='\t', default=Chekc_ObjectId))
    
    
print(sort_name('スマップ'))

No 1
{
	"ended": true,
	"sort_name": "SMAP",
	"_id": "59853e0894b4bd77026d2afe",
	"name": "SMAP",
	"id": 265728,
	"area": "Japan",
	"gid": "6ab7953b-8480-41fe-a9fe-5e220d8e9429",
	"tags": [
		{
			"count": 1,
			"value": "likedis auto"
		}
	],
	"aliases": [
		{
			"sort_name": "\u30b9\u30de\u30c3\u30d7",
			"name": "\u30b9\u30de\u30c3\u30d7"
		}
	],
	"begin": {
		"year": 1988,
		"month": 4
	},
	"type": "Group"
}
None


## 68. ソート
"dance"というタグを付与されたアーティストの中でレーティングの投票数が多いアーティスト・トップ10を求めよ．



In [280]:
import pymongo
import json

conn = pymongo.MongoClient(host='localhost', port=27017)
db = conn.artists
co = db.info

ranking = co.find({'tags.value': 'dance'}).sort('rating.count', -1)

for i, artist in enumerate(ranking[:10], start=1):
    print('Top', i)
    print(json.dumps(artist, indent='\t', default=Chekc_ObjectId))
    print()
    

Top 1
{
	"ended": true,
	"_id": "59853f4494b4bd770273f935",
	"id": 89,
	"gid": "79239441-bfd5-4981-a70c-55c3f15c1287",
	"sort_name": "Madonna",
	"name": "Madonna",
	"gender": "Female",
	"rating": {
		"count": 26,
		"value": 88
	},
	"area": "United States",
	"tags": [
		{
			"count": 1,
			"value": "dance-pop"
		},
		{
			"count": 1,
			"value": "electropop"
		},
		{
			"count": 1,
			"value": "tell me"
		},
		{
			"count": 1,
			"value": "pop and chart"
		},
		{
			"count": 1,
			"value": "multiple ipi"
		},
		{
			"count": 1,
			"value": "electronic"
		},
		{
			"count": 1,
			"value": "am\u00e9ricain"
		},
		{
			"count": 1,
			"value": "usa"
		},
		{
			"count": 1,
			"value": "singer"
		},
		{
			"count": 1,
			"value": "chanteur"
		},
		{
			"count": 1,
			"value": "american"
		},
		{
			"count": 4,
			"value": "pop"
		},
		{
			"count": 1,
			"value": "greatest hits"
		},
		{
			"count": 1,
			"value": "dance"
		}
	],
	"begin": {
		"year": 1958,
		"date": 16,
		"month": 8
	},
	"t

## 69. Webアプリケーションの作成
ユーザから入力された検索条件に合致するアーティストの情報を表示するWebアプリケーションを作成せよ．アーティスト名，アーティストの別名，タグ等で検索条件を指定し，アーティスト情報のリストをレーティングの高い順などで整列して表示せよ．

In [ ]:
#めんどくさいのでスキップ